In [1]:
# pancake problem
import random 

test_stack = [i for i in range(1, 11)]
random.shuffle(test_stack)
test_stack

[8, 3, 7, 1, 4, 9, 5, 2, 6, 10]

In [2]:
def flip(stack, k):
    """Flips the first k elements of the stack."""
    flipped = stack[:k][::-1] # Cutting the first k elements and reversing them
    rest = stack[k:] # Keeping the rest of the stack unchanged
    return flipped + rest # Concatenating the flipped part with the rest of the stack

In [3]:
flip(test_stack, 5)

[4, 1, 7, 3, 8, 9, 5, 2, 6, 10]

In [4]:
# Cost function
## Could be just the sum...

def calculate_cost(stack):
    """Calculates the cost of flipping a substack."""
    return sum(stack)  # Cost is the sum of the values in the substack

In [5]:
# Heuristic function
## Given Gap Heuristic: the number of stack positions for which the pancake
## at that position is not of adjacent size to the pancake below
def calculate_gap_heuristic(stack):
    """Calculates the gap heuristic for the stack."""   
    gaps = 0
    for i, s in enumerate(stack):
        if i+1 != len(stack): # Avoids IndexError for last pancake
            this_pancake = s
            # Check gaps below
            next_pancake = stack[i+1]
            if abs(this_pancake - next_pancake) > 1: # Gap! Not adjacent
                gaps += 1
    return gaps
        

In [6]:
calculate_gap_heuristic([3,2,5,1,6,4,7]) # matches paper results

5

In [7]:
calculate_gap_heuristic(test_stack)

9

In [8]:
test_stack

[8, 3, 7, 1, 4, 9, 5, 2, 6, 10]

In [9]:
for i in range(1, len(test_stack)): # Loop through insert points
    substack = test_stack[:i]
    cost = calculate_cost(substack)
    poss_stack = flip(test_stack, i)
    heuristic = calculate_gap_heuristic(poss_stack)
    f = cost + heuristic
    print(i, f, cost, heuristic)

1 17 8 9
2 19 11 8
3 27 18 9
4 28 19 9
5 31 23 8
6 41 32 9
7 46 37 9
8 48 39 9
9 54 45 9


In [10]:
import heapq

pq = []

for i in range(1, len(test_stack)): # Loop through insert points
    substack = test_stack[:i] # get substack
    cost = calculate_cost(substack) # calc cost to flip the substack
    poss_stack = flip(test_stack, i) # flip the substack
    print(poss_stack)
    heuristic = calculate_gap_heuristic(poss_stack) # calc heuristic (does this flip make the stack closer?)
    f = cost + heuristic # total a* function cost
    heapq.heappush(pq, (f, i, poss_stack)) # add to priority queue

[8, 3, 7, 1, 4, 9, 5, 2, 6, 10]
[3, 8, 7, 1, 4, 9, 5, 2, 6, 10]
[7, 3, 8, 1, 4, 9, 5, 2, 6, 10]
[1, 7, 3, 8, 4, 9, 5, 2, 6, 10]
[4, 1, 7, 3, 8, 9, 5, 2, 6, 10]
[9, 4, 1, 7, 3, 8, 5, 2, 6, 10]
[5, 9, 4, 1, 7, 3, 8, 2, 6, 10]
[2, 5, 9, 4, 1, 7, 3, 8, 6, 10]
[6, 2, 5, 9, 4, 1, 7, 3, 8, 10]


In [11]:
pq

[(17, 1, [8, 3, 7, 1, 4, 9, 5, 2, 6, 10]),
 (19, 2, [3, 8, 7, 1, 4, 9, 5, 2, 6, 10]),
 (27, 3, [7, 3, 8, 1, 4, 9, 5, 2, 6, 10]),
 (28, 4, [1, 7, 3, 8, 4, 9, 5, 2, 6, 10]),
 (31, 5, [4, 1, 7, 3, 8, 9, 5, 2, 6, 10]),
 (41, 6, [9, 4, 1, 7, 3, 8, 5, 2, 6, 10]),
 (46, 7, [5, 9, 4, 1, 7, 3, 8, 2, 6, 10]),
 (48, 8, [2, 5, 9, 4, 1, 7, 3, 8, 6, 10]),
 (54, 9, [6, 2, 5, 9, 4, 1, 7, 3, 8, 10])]

In [12]:
f, i, stack = heapq.heappop(pq)
stack

[8, 3, 7, 1, 4, 9, 5, 2, 6, 10]

In [13]:
test_stack

[8, 3, 7, 1, 4, 9, 5, 2, 6, 10]

In [14]:
GOLD = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]

In [18]:
def generate_successors(stack, current_cost):
    for i in range(1, len(stack)):
        single_action_cost = calculate_cost(stack[:i])
        poss_stack = flip(stack, i)
        heuristic_score = calculate_gap_heuristic(poss_stack)
        new_current_cost = current_cost + single_action_cost
        f_score = new_current_cost + heuristic_score
        new_state = (poss_stack, new_current_cost)
        heapq.heappush(pq, (f_score, i, new_state))

In [ ]:
pq = []
visited = set()

generate_successors(test_stack, 0)

while len(pq) > 0:
    f_score, i, current_state_tup = heapq.heappop(pq)
    if tuple(current_state_tup[0]) in visited:
        continue

    if current_state_tup[0] == GOLD:
        print(current_state_tup)
        break
    visited.add(tuple(current_state_tup[0]))
    generate_successors(*current_state_tup)    

([8, 3, 7, 1, 4, 9, 5, 2, 6, 10], 8)
([3, 8, 7, 1, 4, 9, 5, 2, 6, 10], 11)
([7, 3, 8, 1, 4, 9, 5, 2, 6, 10], 18)
([1, 7, 3, 8, 4, 9, 5, 2, 6, 10], 19)
([4, 1, 7, 3, 8, 9, 5, 2, 6, 10], 23)
([1, 4, 7, 3, 8, 9, 5, 2, 6, 10], 28)
([3, 7, 8, 1, 4, 9, 5, 2, 6, 10], 28)
([7, 1, 3, 8, 4, 9, 5, 2, 6, 10], 27)
([7, 8, 3, 1, 4, 9, 5, 2, 6, 10], 29)
([1, 7, 8, 3, 4, 9, 5, 2, 6, 10], 30)
([3, 7, 1, 8, 4, 9, 5, 2, 6, 10], 30)
([9, 4, 1, 7, 3, 8, 5, 2, 6, 10], 32)
([7, 1, 4, 3, 8, 9, 5, 2, 6, 10], 35)
([4, 1, 7, 8, 3, 9, 5, 2, 6, 10], 34)
([7, 1, 8, 3, 4, 9, 5, 2, 6, 10], 38)
([3, 1, 7, 8, 4, 9, 5, 2, 6, 10], 38)
([1, 8, 3, 7, 4, 9, 5, 2, 6, 10], 37)
([3, 7, 1, 4, 8, 9, 5, 2, 6, 10], 38)
([5, 9, 4, 1, 7, 3, 8, 2, 6, 10], 37)
([1, 4, 7, 8, 3, 9, 5, 2, 6, 10], 39)
([7, 4, 1, 3, 8, 9, 5, 2, 6, 10], 40)
([2, 5, 9, 4, 1, 7, 3, 8, 6, 10], 39)
([7, 3, 1, 8, 4, 9, 5, 2, 6, 10], 40)
([1, 3, 7, 8, 4, 9, 5, 2, 6, 10], 42)
([1, 7, 4, 3, 8, 9, 5, 2, 6, 10], 43)
([4, 1, 8, 3, 7, 9, 5, 2, 6, 10], 41)
([3, 7, 4, 1,